<a href="https://colab.research.google.com/github/ShangWeiKuo/Portfolio/blob/main/Python/Anomaly%20Detection/Anomaly_detection_Machine_temperature_system_failure.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install pycaret

     |████████████████████████████████| 264 kB 38.1 MB/s 
     |████████████████████████████████| 80 kB 9.7 MB/s 
     |████████████████████████████████| 248 kB 52.9 MB/s 
     |████████████████████████████████| 14.6 MB 73 kB/s 
     |████████████████████████████████| 56 kB 4.8 MB/s 
     |████████████████████████████████| 2.0 MB 58.8 MB/s 
     |████████████████████████████████| 1.7 MB 28.5 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 271 kB 55.4 MB/s 
     |████████████████████████████████| 111 kB 62.3 MB/s 
     |████████████████████████████████| 1.3 MB 37.2 MB/s 
     |████████████████████████████████| 6.8 MB 28.9 MB/s 
     |████████████████████████████████| 167 kB 80.2 MB/s 
     |████████████████████████████████| 62 kB 823 kB/s 
     |████████████████████████████████| 675 kB 53.2 MB/s 
     |████████████████████

In [ ]:
import numpy as np 
import pandas as pd 
import plotly.express as px
from pycaret.anomaly import *
import plotly.graph_objects as go
from sklearn.metrics import f1_score, precision_score, recall_score
import os
# set current working directory
path="/content/drive/MyDrive/Anomaly detection/"
os.chdir(path)

In [ ]:
df = pd.read_csv("machine_temperature_system_failure.csv")
df.head()

timestamp      value
0  2013-12-02 21:15:00  73.967322
1  2013-12-02 21:20:00  74.935882
2  2013-12-02 21:25:00  76.124162
3  2013-12-02 21:30:00  78.140707
4  2013-12-02 21:35:00  79.329836

In [ ]:
df['timestamp'] = pd.to_datetime(df['timestamp'])
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22695 entries, 0 to 22694
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   timestamp  22695 non-null  datetime64[ns]
 1   value      22695 non-null  float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 354.7 KB


In [ ]:
anomaly_points = [
          ["2013-12-10 06:25:00.000000","2013-12-12 05:35:00.000000"],
          ["2013-12-15 17:50:00.000000","2013-12-17 17:00:00.000000"],
          ["2014-01-27 14:20:00.000000","2014-01-29 13:30:00.000000"],
          ["2014-02-07 14:55:00.000000","2014-02-09 14:05:00.000000"]
          ]

In [ ]:
#is anomaly? : True => 1, False => 0
df['anomaly'] = 0

for start, end in anomaly_points:
  df.loc[((df['timestamp'] >= start) & (df['timestamp'] <= end)), 'anomaly'] = 1

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22695 entries, 0 to 22694
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   timestamp  22695 non-null  datetime64[ns]
 1   value      22695 non-null  float64       
 2   anomaly    22695 non-null  int64         
dtypes: datetime64[ns](1), float64(1), int64(1)
memory usage: 532.0 KB


In [ ]:
df.index = df['timestamp']
df.drop(['timestamp'], axis=1, inplace=True)
df.head(5)

value  anomaly
timestamp                              
2013-12-02 21:15:00  73.967322        0
2013-12-02 21:20:00  74.935882        0
2013-12-02 21:25:00  76.124162        0
2013-12-02 21:30:00  78.140707        0
2013-12-02 21:35:00  79.329836        0

In [ ]:
# check anomalies
true_anomaly_df = pd.DataFrame(df)
true_anomaly_df = true_anomaly_df.loc[true_anomaly_df['anomaly'] == 1]
true_anomaly_df.head()

value  anomaly
timestamp                              
2013-12-10 06:25:00  53.886196        1
2013-12-10 06:30:00  54.113727        1
2013-12-10 06:35:00  53.514577        1
2013-12-10 06:40:00  54.920342        1
2013-12-10 06:45:00  55.162629        1

In [ ]:
fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Overview of time series data')
fig.add_trace(go.Scatter(x=true_anomaly_df.index, y=true_anomaly_df["value"].to_list(), mode='markers', name='true anomalies'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
s = setup(df, session_id = 123)

Description                 Value
0                               session_id                   123
1                            Original Data            (22695, 2)
2                           Missing Values                 False
3                         Numeric Features                     1
4                     Categorical Features                     1
5                         Ordinal Features                 False
6                High Cardinality Features                 False
7                  High Cardinality Method                  None
8                         Transformed Data            (22695, 3)
9                                 CPU Jobs                    -1
10                                 Use GPU                 False
11                          Log Experiment                 False
12                         Experiment Name  anomaly-default-name
13                                     USI                  e5c0
14                         Imputation Type                simple
15          Iterative Imputation Iteration                  None
16                         Numeric Imputer                  mean
17      Iterative Imputation Numeric Model                  None
18                     Categorical Imputer                  mode
19  Iterative Imputation Categorical Model                  None
20           Unknown Categoricals Handling        least_frequent
21                               Normalize                 False
22                        Normalize Method                  None
23                          Transformation                 False
24                   Transformation Method                  None
25                                     PCA                 False
26                              PCA Method                  None
27                          PCA Components                  None
28                     Ignore Low Variance                 False
29                     Combine Rare Levels                 False
30                    Rare Level Threshold                  None
31                         Numeric Binning                 False
32                         Remove Outliers                 False
33                      Outliers Threshold                  None
34                Remove Multicollinearity                 False
35             Multicollinearity Threshold                  None
36             Remove Perfect Collinearity                 False
37                              Clustering                 False
38                    Clustering Iteration                  None
39                     Polynomial Features                 False
40                       Polynomial Degree                  None
41                    Trignometry Features                 False
42                    Polynomial Threshold                  None
43                          Group Features                 False
44                       Feature Selection                 False
45                Feature Selection Method               classic
46            Features Selection Threshold                  None
47                     Feature Interaction                 False
48                           Feature Ratio                 False
49                   Interaction Threshold                  None

In [ ]:
# check list of available models
# from pycaret.anomaly import *
models()

Name                    Reference
ID                                                                       
abod            Angle-base Outlier Detection        pyod.models.abod.ABOD
cluster       Clustering-Based Local Outlier      pyod.models.cblof.CBLOF
cof         Connectivity-Based Local Outlier          pyod.models.cof.COF
iforest                     Isolation Forest  pyod.models.iforest.IForest
histogram  Histogram-based Outlier Detection        pyod.models.hbos.HBOS
knn             K-Nearest Neighbors Detector          pyod.models.knn.KNN
lof                     Local Outlier Factor          pyod.models.lof.LOF
svm                   One-class SVM detector      pyod.models.ocsvm.OCSVM
pca             Principal Component Analysis          pyod.models.pca.PCA
mcd           Minimum Covariance Determinant          pyod.models.mcd.MCD
sod               Subspace Outlier Detection          pyod.models.sod.SOD
sos             Stochastic Outlier Selection          pyod.models.sos.SOS

In [ ]:
# Train model 1 - Clustering-Based Local Outlier
cluster = create_model('cluster')
cluster_results = assign_model(cluster)
df["anomaly_clo"] = cluster_results['Anomaly']

# check anomalies
clo_anomaly_df = pd.DataFrame(df)
clo_anomaly_df = clo_anomaly_df.loc[clo_anomaly_df['anomaly_clo'] == 1]

clo_f1 = f1_score(df['anomaly'], df['anomaly_clo'])
clo_precision = precision_score(df['anomaly'], df['anomaly_clo'])
clo_recall = recall_score(df['anomaly'], df['anomaly_clo'])

fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Unsupervised anomaly detection in machine temperature system failure(Clustering-Based Local Outlier)')
fig.add_trace(go.Scatter(x=clo_anomaly_df.index, y=clo_anomaly_df["value"].to_list(), mode='markers', name='anomalies'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
# Train model 2 - Isolation Forest
if_cluster = create_model('iforest')
if_cluster_results = assign_model(if_cluster)
df["anomaly_if"] = if_cluster_results['Anomaly']

# check anomalies
if_anomaly_df = pd.DataFrame(df)
if_anomaly_df = if_anomaly_df.loc[if_anomaly_df['anomaly_if'] == 1]

if_f1 = f1_score(df['anomaly'], df['anomaly_if'])
if_precision = precision_score(df['anomaly'], df['anomaly_if'])
if_recall = recall_score(df['anomaly'], df['anomaly_if'])

fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Unsupervised anomaly detection in machine temperature system failure(Isolation Forests)')
fig.add_trace(go.Scatter(x=if_anomaly_df.index, y=if_anomaly_df["value"].to_list(), mode='markers', name='anomalies'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
# Train model 3 - Local Outlier Factor
lof_cluster = create_model('lof')
lof_cluster_results = assign_model(lof_cluster)
df["anomaly_lof"] = lof_cluster_results['Anomaly']

# check anomalies
lof_anomaly_df = pd.DataFrame(df)
lof_anomaly_df = lof_anomaly_df.loc[lof_anomaly_df['anomaly_lof'] == 1]

lof_f1 = f1_score(df['anomaly'], df['anomaly_lof'])
lof_precision = precision_score(df['anomaly'], df['anomaly_lof'])
lof_recall = recall_score(df['anomaly'], df['anomaly_lof'])

fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Unsupervised anomaly detection in machine temperature system failure(Local Outlier Factor)')
fig.add_trace(go.Scatter(x=lof_anomaly_df.index, y=lof_anomaly_df["value"].to_list(), mode='markers', name='anomalies'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
# Train model 4 - One-class SVM detector
svm_cluster = create_model('svm')
svm_cluster_results = assign_model(svm_cluster)
df["anomaly_svm"] = svm_cluster_results['Anomaly']

# check anomalies
svm_anomaly_df = pd.DataFrame(df)
svm_anomaly_df = svm_anomaly_df.loc[svm_anomaly_df['anomaly_svm'] == 1]

svm_f1 = f1_score(df['anomaly'], df['anomaly_svm'])
svm_precision = precision_score(df['anomaly'], df['anomaly_svm'])
svm_recall = recall_score(df['anomaly'], df['anomaly_svm'])

fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Unsupervised anomaly detection in machine temperature system failure(One-class SVM detector)')
fig.add_trace(go.Scatter(x=svm_anomaly_df.index, y=svm_anomaly_df["value"].to_list(), mode='markers', name='anomalies'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
fig = px.line(df, x=df.index, y='value', labels={"value": "Temperature"}, title='Unsupervised anomaly detection in machine temperature system failure - Overview')
fig.add_trace(go.Scatter(x=true_anomaly_df.index, y=true_anomaly_df["value"].to_list(), mode='markers', name='true'))
fig.add_trace(go.Scatter(x=clo_anomaly_df.index, y=clo_anomaly_df["value"].to_list(), mode='markers', name='Clustering-Based Local Outlier'))
fig.add_trace(go.Scatter(x=if_anomaly_df.index, y=if_anomaly_df["value"].to_list(), mode='markers', name='Isolation Forests'))
fig.add_trace(go.Scatter(x=lof_anomaly_df.index, y=lof_anomaly_df["value"].to_list(), mode='markers', name='Local Outlier Factor'))
fig.add_trace(go.Scatter(x=svm_anomaly_df.index, y=svm_anomaly_df["value"].to_list(), mode='markers', name='One-class SVM detector'))
fig.update_xaxes(rangeslider_visible=True)
fig

In [ ]:
# Evaluation
eval_df = np.array(
            [
              [round(clo_f1, 2), round(clo_precision, 2), round(clo_recall, 2)], 
              [round(if_f1, 2), round(if_precision, 2), round(if_recall, 2)],
              [round(lof_f1, 2), round(lof_precision, 2), round(lof_recall, 2)],
              [round(svm_f1, 2), round(svm_precision, 2), round(svm_recall, 2)]
            ]
          )

eval_df = pd.DataFrame(eval_df, columns=['F1 Score', 'Precision Score', 'Recall Score'])
rowname = np.array(['Clustering-Based Local Outlier', 'Isolation Forest', 'Local Outlier Factor', 'One-Class SVM'])
eval_df.index = rowname
eval_df

F1 Score  Precision Score  Recall Score
Clustering-Based Local Outlier      0.53             0.80          0.40
Isolation Forest                    0.55             0.83          0.42
Local Outlier Factor                0.12             0.18          0.09
One-Class SVM                       0.51             0.77          0.38